In [439]:
import pandas as pd

# insert a dataframe object
dfp = pd.DataFrame(pd.read_csv("Results_21Mar2022_md.csv"))
dfp.head()

mc_run_id           grouping  mean_ghgs  mean_land  mean_watscar  \
0          1  fish_female_20-29   5.421821   8.612772   14165.86240   
1          1  fish_female_30-39   5.436673   8.680248   15222.77063   
2          1  fish_female_40-49   5.289333   8.467723   15818.80068   
3          1  fish_female_50-59   5.169020   8.219199   16962.06009   
4          1  fish_female_60-69   5.380268   8.570718   18212.66232   

    mean_eut  mean_ghgs_ch4  mean_ghgs_n2o    mean_bio  mean_watuse  ...  \
0  23.945372       1.164643       0.343663  476.270413   679.923479  ...   
1  24.305262       1.154118       0.326868  467.923201   709.343785  ...   
2  24.191105       1.108404       0.310324  438.659832   707.925368  ...   
3  24.748154       1.032501       0.298130  395.787622   720.825105  ...   
4  25.559430       1.098828       0.310735  421.176867   749.392826  ...   

     sd_eut  sd_ghgs_ch4  sd_ghgs_n2o      sd_bio   sd_watuse   sd_acid  \
0  8.167013     0.632547     0.146827  283.883428  249.472563  8.231176   
1  8.467858     0.601941     0.130298  270.247108  277.927269  7.947014   
2  8.107006     0.572941     0.119872  252.415063  275.760515  8.103589   
3  9.514028     0.509689     0.104731  209.566722  310.422445  8.712428   
4  9.258068     0.609398     0.113401  264.599257  315.922570  8.616601   

   n_participants     sex  diet_group  age_group  
0            1329  female        fish      20-29  
1            2024  female        fish      30-39  
2            1689  female        fish      40-49  
3             946  female        fish      50-59  
4             492  female        fish      60-69  

[5 rows x 24 columns]

data:

- mean_ghgs
- mean_land
- mean_watscar
- mean_eut
- mean_ghgs_ch4
- mean_ghgs_n2o
- mean_bio
- mean_watuse
- mean_acid
  ["mean_ghgs","mean_land","mean_watscar","mean_eut","mean_ghgs_ch4","mean_ghgs_n2o","mean_bio","mean_watuse","mean_acid"]

group by:

- age_group ["20-29","30-39","40-49","50-59","60-69","70-79"]
- sex ["male","female"]
- diet_group ["meat100","meat50","meat","fish","veggie","vegan"]

?:
n_participants

TODO:
-radar chart: calculate mean of each column of each group again?
box plot/ANOVA (follow paper: file:///Users/ne/Downloads/s43016-023-00795-w.pdf)
-ttest
tree map: sex>age>diet group
population-pyramis / violin
heat map> gender[age][group][mean_*]: same block size different color & hue
(diagnal line in each block to seperate gender size):
color: mean\_\* value
area size: participant
pros: can see trend in each age/group

so called advance charts: Treemap, Scatterplot, Area Chart, or Stacked Bar Chart


In [ ]:
data = dfp.copy()

age_group = ["20-29", "30-39", "40-49", "50-59", "60-69", "70-79"]
diet_group = ["fish", "meat", "meat50", "meat100", "vegan", "veggie"]
value_group = [
    "mean_ghgs",
    "mean_land",
    "mean_watscar",
    "mean_eut",
    "mean_ghgs_ch4",
    "mean_ghgs_n2o",
    "mean_bio",
    "mean_watuse",
    "mean_acid",
]

# TODO: sync hovering, try other colorscale, Reduce size so it can display on github

In [444]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np


def plotSubGraph(sex, value, parent_figure, row, column):
    # Loop through the Age Groups and Diet Groups to create boxes
    for y, age in enumerate(age_group):  # Use age group as y axis
        for x, diet in enumerate(diet_group):  # Use diet group as x axis
            # Filtering data
            group_df = data[
                (data["sex"] == sex)
                & (data["age_group"] == age)
                & (data["diet_group"] == diet)
            ]
            group_data = group_df.values

            # Define text when hovering on sample (data point)
            text_values = []
            for i in range(len(group_df.values)):  # Columns (diet groups)
                sample = group_df.iloc[i]
                text = f"<br>Run ID: {sample['mc_run_id']}<br>Age: {age}<br>Diet: {diet}<br>Mean: {sample[value]}"
                text_values.append(text)

            # Create Heatmap with data of each run and value
            startPoint = x - 0.5
            size = len(group_data)
            unitWidth = 1 / size
            parent_figure.add_trace(
                go.Heatmap(
                    x=[
                        startPoint,  # first point position
                        startPoint + unitWidth,  # second point position
                    ],
                    y=[y],
                    z=[group_df[value].values],
                    text=[text_values],
                    hoverinfo="text",
                    coloraxis="coloraxis",
                ),
                row=row,
                col=column,
            )

    # Create Borders
    # Vertical lines
    for y in range(0, len(diet_group) + 1):
        parent_figure.add_shape(
            type="line",
            x0=y - 0.5 - (unitWidth / 2),
            x1=y - 0.5 - (unitWidth / 2),  # Vertical position
            y0=-0.5,
            y1=len(age_group) - 0.5,  # Cover all rows
            line=dict(color="white", width=0.5),
            row=row,
            col=column,
        )

    # Horizontal lines
    for y in range(0, len(age_group) + 1):
        parent_figure.add_shape(
            dict(
                type="line",
                x0=-0.5 - (unitWidth / 2),
                x1=len(diet_group) - 0.5 - (unitWidth / 2),  # Cover all columns
                y0=y - 0.5,
                y1=y - 0.5,  # Horizontal position
                line=dict(color="white", width=0.5),
            ),
            row=row,
            col=column,
        )


def plotGraph(value):
    # Create a parent figure with 1x2 subplots (for female and male)
    parent_fig = make_subplots(rows=1, cols=2, subplot_titles=["Female", "Male"])
    plotSubGraph("female", value, parent_fig, row=1, column=1)
    plotSubGraph("male", value, parent_fig, row=1, column=2)

    # Setup parent figure layout
    parent_fig.update_layout(
        title=value,
        title_x=0.5,
        showlegend=False,
        coloraxis=dict(
            colorscale="Viridis",
            showscale=True,
        ),
        height=720,
        width=1080,
    )

    parent_fig.update_xaxes(tickvals=np.arange(len(diet_group)), ticktext=diet_group)
    parent_fig.update_yaxes(tickvals=np.arange(len(age_group)), ticktext=age_group)

    parent_fig.show()


plotGraph("mean_ghgs")
plotGraph("mean_watscar")

In [445]:
for value in value_group:
    plotGraph(value)
